# Quantum Circuit Design through Monte Carlo Tree Search
In this tutorial we are going to show the whole pipeline of the Monte Carlo Tree Search (MCTS) implemented for quantum circuit design.
The goal is the design of a quantum circuit that solve a certain problem. A random quantum circuit is showed below.

In [32]:
# Import library that allow to work with quantum circuits
from qiskit import QuantumCircuit

# Initialize a quantum circuit with 4 qubits
qc = QuantumCircuit(4)
# Add a non-parameterized gate on the 0th qubit 
qc.h(0)
# Add a parameterized gate on each of the four qubits (all with a parameter fixed to 0.5)
for i in range(4):
    qc.ry(0.5, i)
print("You have built your first quantum circuit:")
qc.draw()

# If you want to print the circuit in a fancier way uncomment replace the previous line of code with the following one
# qc.draw("mpl")

You have built your first quantum circuit:


┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘

Designing a quantum circuit means finding the ordered sequence of gates (parameterized and not-parameterized) applied to the qubits that give raise to the circuit that can solve the given problem.
You can imagine the task of designing a quantum circuit as the quantum analogue of the design of Neural Networks. In neural networks you have to find the stucture (number of neurons, hidden layers, activation function, etc.) that allows to solve the problem after the learning of the parameters (weights). In quantum circuit, we also have to find the structure (sequence of gates), that allows to solve the problem after the learning of the parameters (angle parameters of the parameterized gates).
However the search space defined by quantum circuits is extremely big and we want to find automatic and efficient way to get an efficient and perfomant circuit. Namely we want a shallow circuit that evaluated on the objevtive function gives a value close to the optimum.

In this project, we will provide you some problems encoded in the circuit-based quantum computing setting in a black-box form. That means, that the problems are provided as real-valued function on the domain of quantum circuits. This functions will be your objective function and your goal is to minimize them.

You don't have to understand what exactly those "quantum" functions do, but you only need to work with MCTS and its variants to get hopefully better results (lower values of the objective functions).

## Problem Definition


Here we define an objective function to optimize. The objective function is a real-valued function defined on quantum circuits. You can find examples in the field of quantum chemistry, systems of linear equations, Sudoku and on random quantum circuit in the file evaluation_functions.py. 

Let's take as example the a famous example from the domain of quantum chemistry. In order to study molecule is important to estimate their ground state energy. We are going to use an hybrid classical-quantum algorithm, the variational quantum eigensolver, to estimate the ground state energy of the hydrogen molecule $H_2$. In the following evaluate the quantum circuit created above as a solution for this specific problem.

In [33]:

import evaluation_functions as evf

problem = evf.h2
cost_value = problem(qc, cost=True)

print(f"Given the quantum circuit below: \n{qc}\n the objective function returns: {cost_value}")

Given the quantum circuit below: 
        ┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘           
 the objective function returns: -0.2318460796537938


## Link Quantum to Classical
Once we have defined the problem, we can use MCTS in order to design a first guess, also known as "ansatz", for the initial quantum circuit that.
We hope you did not get scared with this brief intro into the "quantum world". Anyways, from now on you will only work with classical techniques. Here there is the link we created between the classical and quantum "world":
- Node: Quantum Circuit
- Moves: apply changes to the circuit. There are 4 possible changes implemented:
    1. Add new random gate in random position
    2. Remove radom gate in random position
    3. Swap a random gate with a new gate in the same position
    4. Change the angle parameter in a parameterized gate
- Objective function: quantum black box provided


    


## Your MCTS baseline
Below you will see how does your baseline work

In [34]:
# Number of qubits required by the problem. In the problem of estimating the ground state energy of the ydrogen we only need 4 qubits (For all the other problems we provide you of all the information)
variable_qubits = 4
ancilla_qubits = 0
# Max depth of the circuit that we want to search with the MCTS
max_depth = 10
# Computational budget we provide MCTS to explore the search space. it is equivalent to the number of new nodes evaluated
budget = 1000
# Set to false MCTS use an adaptive technique to fix the branching factor of each node. This allows to explore more the most promising nodes. Set to an integer, the branching factor will be fixed for all nodes of the tree.
branches = False

criteria = "average_value"
rollout_type = 'classic'
roll_out_steps = 2
choices = {'a': 50, 'd': 10, 's': 20, 'c': 20, 'p': 0}
epsilon = None
stop_deterministic = False
# Hyperparametrs of MCTS
ucb = 0.4
pw_C = 1
pw_alpha = 0.3


Below we define the root node by inizializing an empty circuit. The search starts from that node and MCTS will search for the best.

In [35]:
import mcts
from structure import Circuit
# Initialize the search by creating an empty circuit in the root node
root = mcts.Node(Circuit(variable_qubits=variable_qubits, ancilla_qubits=ancilla_qubits), max_depth=max_depth)
        
best_path = mcts.mcts(root, budget=budget, branches=branches, evaluation_function=problem, criteria=criteria, rollout_type=rollout_type, roll_out_steps=roll_out_steps,
                                choices=choices, epsilon=epsilon, stop_deterministic=stop_deterministic, ucb_value=ucb, pw_C=pw_C, pw_alpha=pw_alpha, verbose=True)

Root Node:
 Tree depth: 0  -  Generated by Action: None  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐
v_0: ┤ H ├
     ├───┤
v_1: ┤ H ├
     ├───┤
v_2: ┤ H ├
     ├───┤
v_3: ┤ H ├
     └───┘
Epoch Counter:  0
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐              
v_0: ┤ H ├──────────────
     ├───┤              
v_1: ┤ H ├──────────────
     ├───┤              
v_2: ┤ H ├──────────────
     ├───┤┌────────────┐
v_3: ┤ H ├┤ Rx(3.6765) ├
     └───┘└────────────┘
Reward:  0.042078979774733405
Epoch Counter:  1
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 1):
     ┌───┐     
v_0: ┤ H ├─────
     ├───┤┌───┐
v_1: ┤ H ├┤ X ├
     ├───┤└─┬─┘
v_2: ┤ H ├──┼──
     ├───┤  │  
v_3: ┤ H ├──■──
     └───┘     
Reward:  0.042078979

Finally it outputs the path that creates the best circuit, starting from the root to the leaf. In the following we print the values of the objective function evaluated on the quantum circuits designed along the best path. Note that, in this formulation, a children node is not necessarily better than the parent.
Remember that this is a minimization problem and the lower the objective value the better the node

In [36]:
quantum_circuit_path = best_path['qc']
cost = []
for i in range(len(quantum_circuit_path)):
    cost.append(problem(quantum_circuit_path[i], cost=True))
    print("Node at depth tree: ", i, "number of children: ", best_path["children"][i])
    print("Objective value: ", cost[i])
    print("Cumulative Reward: ", best_path["value"][i])
    print("Average Reward: ", best_path["value"][i]/best_path["visits"][i], "\n")

Node at depth tree:  0 number of children:  4
Objective value:  -0.04207897977473338
Cumulative Reward:  283.76651575017223
Average Reward:  0.2834830327174548 

Node at depth tree:  1 number of children:  4
Objective value:  -0.04207897977473338
Cumulative Reward:  283.48461099039304
Average Reward:  0.29437654308452027 

Node at depth tree:  2 number of children:  4
Objective value:  -0.18522212650016961
Cumulative Reward:  282.3054420676687
Average Reward:  0.3022542206291956 

Node at depth tree:  3 number of children:  4
Objective value:  -0.22546628639141258
Cumulative Reward:  277.4512124318887
Average Reward:  0.3093101587869439 

Node at depth tree:  4 number of children:  4
Objective value:  -0.22546628639141253
Cumulative Reward:  275.66210721386545
Average Reward:  0.31325239456121073 

Node at depth tree:  5 number of children:  3
Objective value:  -0.22491661315384776
Cumulative Reward:  6.328911143435042
Average Reward:  0.39555694646469014 

Node at depth tree:  6 numbe

At this poit we selct the ansatz as the best quantum circuit found in the path.

In [37]:
ansatz = quantum_circuit_path[cost.index(min(cost))]
print("Selected Ansatz: \n", ansatz)

Selected Ansatz: 
      ┌───┐┌─────────────┐                   
v_0: ┤ H ├┤ Ry(0.93648) ├───────────────────
     ├───┤└────┬───┬────┘┌────────────┐┌───┐
v_1: ┤ H ├─────┤ X ├─────┤ Ry(1.6239) ├┤ X ├
     ├───┤     └─┬─┘     ├───────────┬┘└─┬─┘
v_2: ┤ H ├───────┼───────┤ Rz(5.609) ├───■──
     └───┘       │       ├───────────┴┐     
v_3: ────────────■───────┤ Rz(3.8891) ├─────
                         └────────────┘     


## Parameter Optimization
Once we designed the structure of our quantum circuit we optimize the parameters through a classical gradient-based optimizer. Here we chose the ADAM Optimizer

In [38]:
problem(quantum_circuit=ansatz, gradient=True)

Step = 0,  Energy = -0.73258950 Ha
Step = 2,  Energy = -0.73667816 Ha
Step = 4,  Energy = -0.74058134 Ha
Step = 6,  Energy = -0.74431137 Ha
Step = 8,  Energy = -0.74789551 Ha
Step = 10,  Energy = -0.75135733 Ha
Step = 12,  Energy = -0.75469959 Ha
Step = 14,  Energy = -0.75791075 Ha
Step = 16,  Energy = -0.76097779 Ha
Step = 18,  Energy = -0.76389325 Ha
Step = 20,  Energy = -0.76665712 Ha
Step = 22,  Energy = -0.76927445 Ha
Step = 24,  Energy = -0.77175049 Ha
Step = 26,  Energy = -0.77408720 Ha
Step = 28,  Energy = -0.77628369 Ha
Step = 30,  Energy = -0.77833904 Ha
Step = 32,  Energy = -0.78025475 Ha
Step = 34,  Energy = -0.78203511 Ha
Step = 36,  Energy = -0.78368578 Ha
Step = 38,  Energy = -0.78521193 Ha
Step = 40,  Energy = -0.78661758 Ha
Step = 42,  Energy = -0.78790644 Ha
Step = 44,  Energy = -0.78908308 Ha
Step = 46,  Energy = -0.79015325 Ha
Step = 48,  Energy = -0.79112324 Ha
Step = 50,  Energy = -0.79199911 Ha
Step = 52,  Energy = -0.79278637 Ha
Step = 54,  Energy = -0.79349041 

[array(-0.73047581),
 array(-0.7325895),
 array(-0.73465714),
 array(-0.73667816),
 array(-0.73865258),
 array(-0.74058134),
 array(-0.74246652),
 array(-0.74431137),
 array(-0.7461198),
 array(-0.74789551),
 array(-0.74964103),
 array(-0.75135733),
 array(-0.75304396),
 array(-0.75469959),
 array(-0.75632245),
 array(-0.75791075),
 array(-0.75946293),
 array(-0.76097779),
 array(-0.76245464),
 array(-0.76389325),
 array(-0.76529389),
 array(-0.76665712),
 array(-0.76798372),
 array(-0.76927445),
 array(-0.77052992),
 array(-0.77175049),
 array(-0.77293628),
 array(-0.7740872),
 array(-0.77520306),
 array(-0.77628369),
 array(-0.77732899),
 array(-0.77833904),
 array(-0.77931414),
 array(-0.78025475),
 array(-0.7811615),
 array(-0.78203511),
 array(-0.78287631),
 array(-0.78368578),
 array(-0.78446415),
 array(-0.78521193),
 array(-0.7859296),
 array(-0.78661758),
 array(-0.78727635),
 array(-0.78790644),
 array(-0.78850846),
 array(-0.78908308),
 array(-0.78963108),
 array(-0.79015325